# Universidade Federal do Rio Grande do Norte
## Programa de Pós-graduação em Engenharia Elétrica e de Computação
### Course: Tópicos Especiais C
### Professor: Ivanovitch Silva
### Students: 

* Aguinaldo Bezerra Batista Júnior
* Pedro Klisley Ferreira da Silva
* Ycaro Ravel Dantas

#### Activity: Task 2, Project 1
#### Subject: Analyzing Population Estimation of the states of northeast region of Brazil
#### Objectives: 
#### Dataset: population_2017.csv

In [4]:
import os
import folium
import json
import pandas as pd
from branca.colormap import linear
import numpy as np
from shapely.geometry import Polygon
from shapely.geometry import Point
from numpy import random


In [5]:
# dataset name
dataset_pop_2017 = os.path.join('data', 'population_2017.csv')

# read the data to a dataframe
data2017 = pd.read_csv(dataset_pop_2017)

# eliminate spaces in name of columns
data2017.columns = [cols.replace(' ', '_') for cols in data2017.columns]

data2017.head()


UF  COD._UF  COD._MUNIC      NOME_DO_MUNICÍPIO  POPULAÇÃO_ESTIMADA
0  RO     11.0        15.0  Alta Floresta D'Oeste             25437.0
1  RO     11.0        23.0              Ariquemes            107345.0
2  RO     11.0        31.0                 Cabixi              6224.0
3  RO     11.0        49.0                 Cacoal             88507.0
4  RO     11.0        56.0             Cerejeiras             17934.0

In [6]:
# Defining northest states UF code
NE = ['AL','BA','CE','MA','PB','PE','PI','RN','SE']

# filtering data in NE
dataNE = data2017[data2017['UF'].isin(NE)]

# sort dataset by city name
dataNE = dataNE.sort_values('NOME_DO_MUNICÍPIO')

dataNE.head()
                  


UF  COD._UF  COD._MUNIC NOME_DO_MUNICÍPIO  POPULAÇÃO_ESTIMADA
891   CE     23.0       101.0           Abaiara             11605.0
1828  BA     29.0       207.0             Abaré             20189.0
1827  BA     29.0       108.0            Abaíra              9199.0
1465  PE     26.0        54.0      Abreu e Lima             99364.0
1829  BA     29.0       306.0         Acajutiba             15727.0

In [7]:
# searching the files in geojson/geojs-xx-mun.json
br_states = os.path.join('geojson', 'geojs-100-mun.json')

# load the data and use 'latin-1'encoding because the accent
geo_json_data = json.load(open(br_states,encoding='latin-1'))

In [8]:
# http://cidades.ibge.gov.br/painel/historico.php?codmun=241030
# Presidente Juscelino city changes your name to Serra Caiada
geo_json_data['features'][112]['properties']['description'] = 'Serra Caiada'
geo_json_data['features'][112]['properties']['name'] = 'Serra Caiada'

In [9]:
geo_json_ne  = geo_json_data.copy()
ne_prefixes = ['21','22','23','24','25','26','27','28','29']

geo_json_ne['features'] = \
[city for city in geo_json_data['features'] if str(city['properties']['id']).startswith(tuple(ne_prefixes))]

In [10]:
# Create a map object
m = folium.Map(
    location=[-5.826592, -35.212558],
    zoom_start=5,
    tiles='Stamen Terrain'
)

# Configure geojson layer
folium.GeoJson(geo_json_ne).add_to(m)

m

In [13]:
# colormap yellow and green (YlGn)
colormap = linear.YlGn.scale(
    dataNE.POPULAÇÃO_ESTIMADA.min(),
    dataNE.POPULAÇÃO_ESTIMADA.max())

print(colormap(5000.0))

colormap

#ffffcc


In [19]:
populationne_dict = dataNE.set_index('NOME_DO_MUNICÍPIO')['POPULAÇÃO_ESTIMADA']

#population-ne_dict.

In [20]:
# Create a map object
m = folium.Map(
    location=[-5.826592, -35.212558],
    zoom_start=5,
    tiles='Stamen Terrain'
)

# Configure geojson layer
folium.GeoJson(
    geo_json_ne,
    name='Population estimation of NE Region in 2017',
    style_function=lambda feature: {
        'fillColor': colormap(populationne_dict[feature['properties']['description']]),
        'color': 'black',
        'weight': 0.5,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(m)

colormap.caption = 'NE Region Population estimation (2017)'
colormap.add_to(m)

folium.LayerControl().add_to(m)

m

ValueError: The truth value of a Series is ambiguous. Use a.empty, a.bool(), a.item(), a.any() or a.all().